Evaluation Pipeline for XGboost with Embedding features


Install the required model and change the data and model path

In [6]:
!pip install -U FlagEmbedding
from FlagEmbedding import BGEM3FlagModel
model = BGEM3FlagModel('BAAI/bge-m3', use_fp16=True)

Fetching 30 files:   0%|          | 0/30 [00:00<?, ?it/s]

In [4]:
#import pandas as pd
import xgboost as xgb
from sklearn.metrics import accuracy_score, classification_report

csv_file_path = '/content/drive/Shared drives/5190_NLP_Project/test_data_random_subset.csv'
model_path = '/content/drive/Shared drives/5190_NLP_Project/xgboost_model/final_xgboost_model.json'

data = pd.read_csv(csv_file_path, index_col=0)

titles = data['title'].tolist()
labels = data['labels'].tolist()

labels = [1 if label == 0 else 0 for label in labels]

batch_size = 32
embeddings = []

print('Encoding titles...')
for i in range(0, len(titles), batch_size):
    batch = titles[i:i + batch_size]
    batch_embeddings = model.encode(batch, batch_size=batch_size, max_length=512)['dense_vecs']
    embeddings.extend(batch_embeddings)
    print(f"Processed {i + len(batch)}/{len(titles)} titles")

embeddings_df = pd.DataFrame(embeddings)
embeddings_df['label'] = labels

X = embeddings_df.iloc[:, :-1].values
y = embeddings_df['label'].values


print('Loading XGBoost model...')
xgboost_model = xgb.XGBClassifier()
xgboost_model.load_model(model_path)

print('Making predictions...')
y_pred_prob = xgboost_model.predict(X)
y_pred = (y_pred_prob >= 0.5).astype(int)

print("\nModel Performance:")
accuracy = accuracy_score(y, y_pred)
print(f"Accuracy: {accuracy:.4f}")

print("\nClassification Report:\n", classification_report(y, y_pred))



You're using a XLMRobertaTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


Encoding titles...
Processed 20/20 titles
Loading XGBoost model...
Making predictions...

Model Performance:
Accuracy: 0.7500

Classification Report:
               precision    recall  f1-score   support

           0       0.73      0.80      0.76        10
           1       0.78      0.70      0.74        10

    accuracy                           0.75        20
   macro avg       0.75      0.75      0.75        20
weighted avg       0.75      0.75      0.75        20

